In [ ]:
pip install diffusers

In [2]:
import pandas as pd 
from diffusers import AudioLDMPipeline
import torch
import scipy

In [ ]:
repo_id = "cvssp/audioldm-s-full-v2"
pipe = AudioLDMPipeline.from_pretrained(repo_id, torch_dtype=torch.float16)
pipe = pipe.to("cuda")

In [4]:
template = "a {} talking"
negative_prompt = "low quality, average quality"

In [5]:
df = pd.read_csv("/kaggle/input/new-data/Bias_Types_Term_Category.csv")

In [ ]:
df.head()

In [9]:
def generate_and_save(term, start_idx=0, number=100):
    descriptions = [template.format(term) for _ in range(number)]
    audios = pipe(
        descriptions,
        audio_length_in_s=5.0,
        guidance_scale=2.5,
        num_inference_steps=10,
        negative_prompt=[negative_prompt] * len(descriptions),
    )["audios"]
    
    for idx, one_wav in enumerate(audios):
        scipy.io.wavfile.write(f'./audio_ldm/{term}_{idx+start_idx}', rate=16000, data=one_wav)


In [ ]:
for idx, rows in df.iterrows():
  if rows['Category'] != 'Religion' and rows['Category'] != 'Portrayal in Media':
    print(idx)
    generate_and_save(rows['Term'], 0, 100)